In [1]:
#from scripts import *

from scripts.default_imports import *



print("imports done")

c:\Users\Ulrik\anaconda3\envs\intro-ai\lib\site-packages\tqdm\auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
c:\Users\Ulrik\anaconda3\envs\intro-ai\lib\site-packages\scipy\__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.1
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"
c:\Users\Ulrik\anaconda3\envs\intro-ai\lib\site-packages\huggingface_hub\snapshot_download.py:6: FutureWarning: snapshot_download.py has been made private and will no longer be available from version 0.11. Please use `from huggingface_hub import snapshot_download` to import the only public function in this module. Other members of the file may be changed without a deprecation notice.
  warnings.warn(



GPUs detected:          1
Using GPU:              True
Device:                 cuda
Got model from pickle:  True

imports done


In [2]:
# user functions
from scripts.cleaning import *
from scripts.plotting import *
from scripts.topic_finding import *
from scripts.semi_supervised import *

In [3]:
df = pd.read_csv("data/tensorflow.csv", on_bad_lines='skip')

print(df.shape)

df.head(3)

(32469, 7)


commit author_name    time_sec  \
0  8a428cdd35     ekelsen  1524782988   
1  ce733dc348     ekelsen  1524781964   
2  5cd6a8d1ed     ekelsen  1524781835   

                                                                           subject  \
0  Merge-pull-request-18846-from-yongtang-04252018-FloorDiv-int8                     
1  Merge-pull-request-18881-from-ManHyuk-fix_typo                                    
2  Merge-pull-request-18907-from-yongtang-18363-mpi                                  

   files_changed  lines_inserted  lines_deleted  
0            NaN             NaN            NaN  
1            NaN             NaN            NaN  
2            NaN             NaN            NaN

In [4]:
df.isna().sum()

commit               0
author_name          0
time_sec             0
subject              0
files_changed     3324
lines_inserted    4294
lines_deleted     7857
dtype: int64

We are intending to use the `subject` field as a temporary substitue of `categoryRaw` which we wait to get from the schibsted data

In [5]:
# if your computer does not have GPU support, you can use a sample of the dataset instead to make it run in a reasonable time
if device == "cpu": df = df.sample(frac=0.05)

print(df.shape)

df.head(3)

(32469, 7)


commit author_name    time_sec  \
0  8a428cdd35     ekelsen  1524782988   
1  ce733dc348     ekelsen  1524781964   
2  5cd6a8d1ed     ekelsen  1524781835   

                                                                           subject  \
0  Merge-pull-request-18846-from-yongtang-04252018-FloorDiv-int8                     
1  Merge-pull-request-18881-from-ManHyuk-fix_typo                                    
2  Merge-pull-request-18907-from-yongtang-18363-mpi                                  

   files_changed  lines_inserted  lines_deleted  
0            NaN             NaN            NaN  
1            NaN             NaN            NaN  
2            NaN             NaN            NaN

In [6]:
df["subject_clean"] = df["subject"].apply(string_cleaner)

df[["subject", "subject_clean"]].head(5)

subject  \
0  Merge-pull-request-18846-from-yongtang-04252018-FloorDiv-int8                     
1  Merge-pull-request-18881-from-ManHyuk-fix_typo                                    
2  Merge-pull-request-18907-from-yongtang-18363-mpi                                  
3  Merge-pull-request-18896-from-KikaTech-fix_lite_topk                              
4  Fix-cmake-build-issues-with-GPU-on-Linux-18775                                    

                                                                     subject_clean  
0  merge pull request 18846 from yongtang 04252018 floordiv int8                    
1  merge pull request 18881 from manhyuk fix_typo                                   
2  merge pull request 18907 from yongtang 18363 mpi                                 
3  merge pull request 18896 from kikatech fix_lite_topk                             
4  fix cmake build issues with gpu on linux 18775

In [7]:
try:
    embs = pickle.load(open(f'data/embs-{device}.pkl', 'rb'))
    print("loaded embeddings from pickle")
except:
    embs = model.encode(df["subject_clean"].to_numpy())
    pickle.dump(embs, open(f'data/embs-{device}.pkl', 'wb'))
    print("created embeddings from scratch")

loaded embeddings from pickle


In [8]:
try:
    uembs = pickle.load(open(f'data/umap-{device}.pkl', 'rb'))
    print("loaded umap from pickle")
except:
    uembs = UMAP(n_neighbors=20, min_dist=0.1).fit_transform(embs)
    pickle.dump(uembs, open(f'data/umap-{device}.pkl', 'wb'))
    print("created umap from scratch")

loaded umap from pickle


In [9]:
fig = px.scatter(x=uembs[:,0], y=uembs[:,1])

fig.update_layout(width=800, height=800)
fig.update_traces(marker=dict(size=2))

# plotting to show how the embeddings are when just dimensionality reduction is used
fig_show_save(fig, "umap-scatter")

In [10]:
clusters_2d = HDBSCAN(min_cluster_size=100, cluster_selection_method="leaf").fit(uembs)


print(f"""
    2D
    Number of clusters: {len(set(clusters_2d.labels_)) - 1}
    Number of rows as outliers: {clusters_2d.labels_.tolist().count(-1)}
""")


    2D
    Number of clusters: 55
    Number of rows as outliers: 15049



In [11]:
trace_cluster_2d, trace_outlier_2d = result_tracer_wrapper(uembs, clusters_2d.labels_, df["subject_clean"].to_numpy())


col11 = [trace_cluster_2d, trace_outlier_2d]


row1 = [col11]


trace_list = [row1]

fig = subplotter(trace_list, ["Topics by HDBSCAN Cluster", ])

fig_show_save(fig, "topics-by-hdbscan-clusters")

In [12]:
result_2d = result_df_maker(uembs, clusters_2d.labels_, df["subject_clean"].to_numpy())

result_2d[["cluster_label", "topics"]].groupby(["cluster_label", "topics"])["topics"].count().reset_index(name="vidoes_count").sort_values(by="vidoes_count", ascending=False).head(20)

cluster_label                                        topics  vidoes_count
0              -1                    fix add merge request pull         15049
16             15                            xla add tf hlo cpu          1544
39             38               add fix tfdata tf documentation          1300
1               0               generated update docs op python          1256
48             47              remove fix variable add function           843
45             44                        test tests add fix api           818
27             26                      graph add nodes fix node           770
22             21             tensor tensors add tensorflow fix           631
6               5        merge internal changes commit squashed           546
18             17                merge request pull patch gunan           544
2               1                related files update ops pbtxt           495
36             35                build fix add makefile android           446
44             43               add support fix op quantization           410
30             29  fix docstring formatting documentation minor           402
55             54                   add device fix memory queue           380
20             19             tensorboard fix add update plugin           367
23             22             tensorflow build fix core contrib           336
3               2        change internal changes minor breaking           286
38             37                  rnn add fix lstm dynamic_rnn           277
37             36                 gradient gradients add fix op           277

In [13]:
# allwords = list((df["subject_clean"])

# allwords = " ".join(allwords)


df["subject_clean"].apply(lambda x: (x.split(" "))).explode().value_counts().head(20)

# TODO
# get top words
# run stopword filter
# find 20 most common words post stopword filter
# semi supervise on 20 most common words

              941166
to              8273
for             6103
the             5658
in              5346
of              3995
fix             3943
add             3846
from            3711
merge           3530
a               3234
update          3188
and             3098
pull            2414
request         2409
op              1946
python          1837
docs            1572
tensorflow      1553
generated       1546
Name: subject_clean, dtype: int64

based on this, we can try to semi supervise on words like fix, add, merge, update, etc

## Semi Supervised attempt

In [19]:
# plot threshold
threshold = 0.2 # used to be 0.25 for the cleaner clustering

# words to use in semi supervisation
interests = interest_fixer("""
fix add merge remove update pull request python docs tensorflow generated
""")

print(interests)

['fix add merge remove update pull request python docs tensorflow generated']


In [20]:
# getting results
y, similarity = make_dataset(embs, targets=interests, model=model, target_threshold=threshold)

In [21]:
fetch_from_pickle = False
fast = False

if not fetch_from_pickle:
  uemb_semi_s = UMAP(n_neighbors=100, metric="cosine", target_weight=10).fit_transform(embs, y-1) # used to have just nn = 100 at 0.2 similiarity, and not the metric and target weight
  
  pickle.dump( uemb_semi_s, open( f"emb-semi-s-fast-{fast}.pickle", "wb" ) )
else:
  try:
    uemb_semi_s = pickle.load( open( f"emb-semi-s-fast-{fast}.pickle", "rb" ) )
    print("got embs from pickle")
    
  except:
    print(f"no pickle found with fast-{fast}")

In [22]:
cluster_semi_s_hdb = HDBSCAN(min_cluster_size=100, min_samples=20, metric='euclidean', cluster_selection_method='eom').fit(uemb_semi_s)

In [23]:
trace_cluster_2d, trace_outlier_2d = result_tracer_wrapper(uemb_semi_s, cluster_semi_s_hdb.labels_, df["subject_clean"].to_numpy())


col11 = [trace_cluster_2d, trace_outlier_2d]


row1 = [col11]


trace_list = [row1]

fig = subplotter(trace_list, ["Topics by HDBSCAN Cluster", ])

fig_show_save(fig, "topics-by-hdbscan-clusters")